In [ ]:
# ..... build coexp network with pseudobulk exp data ..... #

In [3]:
library(dplyr)

In [8]:
## create coexpression network ## 
build_coexp_network <- function(net, method = "spearman", flag = "rank"){
    
    # Calculate correlation coefficients
    genes = rownames(net)
    net = net[rowSums(net) > 0, ]

#     print(paste0("... ",dim(net)[1]," of ",length(genes), " genes have non-zero expression" ))

    net = cor(t(net), method = method)
    
    # Create network
    temp = net[upper.tri(net, diag = T)]
    if (flag == "abs"){
        temp = abs(temp)
    }
    
#     print("...ranking")
    temp = rank(temp, ties.method = "average")  

#     print("...reconstructing matrix")
    net[upper.tri(net, diag = T)] = temp

    net = t(net)
    net[upper.tri(net, diag = T)] = temp

    net = net / max(net, na.rm = T)
    med = median(net, na.rm = T)

    ind = setdiff(genes, rownames(net))   # which genes are missing?

    temp = matrix(med, length(ind), dim(net)[2])
    rownames(temp) = ind

    net = rbind(net, temp)
    temp = matrix(med, dim(net)[1], length(ind))
    colnames(temp) = ind
    net = cbind(net, temp)

    # reorder to original
    net = net[genes, genes]
    diag(net) = 1

    return(net)
}

In [13]:
currspecies = 'chicken'
currstage = 'stage32'
load(paste0(currstage, '_pseudobulk_expression_matrices.Rdata'))
scbulk1[1:2,]

Cardiomyocytes Endothelial_Capillaries Fibroblasts Immature_Endothelium
SPRY2  15.957658      187.938750              126.012129  49.846995           
PCDH20  1.138833        3.016081                2.160894   3.501757           
       Smooth_Muscle_Cells Pericytes_Stromal Immature_FB-like Pericytes 
SPRY2  37.842986           81.381689         121.919485       297.320854
PCDH20  2.321711            9.952679           3.315353         1.800926
       Endothelial_Venous Endocardial Immature_Cardiomyocytes
SPRY2  86.42703           63.67471    31.546087              
PCDH20 14.99700           18.21777     2.861271              
       Endothelial_Arterial Neuronal_Cells Epicardium_FB-like
SPRY2  46.81140             49.910793      75.5469           
PCDH20 12.93025              4.195126       0.0000

In [14]:
# correlate across all subclasses
options(warn = -1)
cor1 = build_coexp_network(scbulk1, method = 'spearman')
dim(cor1)
cor1[1:3,1:3]

# save
fileo = paste0(currspecies, '_', currstage, '_coexp_net.Rdata')
save(cor1, file = fileo)

[1] 17007 17007

SPRY2     PCDH20    NDFIP2   
SPRY2  1.0000000 0.4618882 0.8700265
PCDH20 0.4618882 1.0000000 0.9648554
NDFIP2 0.8700265 0.9648554 1.0000000